In [1]:
import pandas as pd
import requests
import json
import re
import numpy as np
import random
import pymongo

In [383]:
df=pd.read_excel('crime_o.xls',skiprows=4,skipfooter=8)
df=df.dropna(subset=['County'])
df['State']=df['State'].ffill()
new =df['State'].str.split(" -",n = 1, expand = True)
df['State']=new[0]
df.columns = ['State', 'County', 'Violent_Crime', 'Murder', 'Rape',
              'Robbery', 'Aggravated_Assault', 'Property_crime','Burglary',
              'Larceny-theft', 'Motor_vehicle_theft','Arson']
df=df.fillna(0)
df=df.reset_index(drop=True)
df.to_csv('crime.csv')

In [374]:
df1=pd.read_excel('GDP_o.xlsx',skiprows=3,skipfooter=3)
df1.insert(0, "col0",np.nan)
df1=df1[["col0",'Unnamed: 0',2019,'2020.1','2020.2','2020.3']]
df1.columns = ['State','County','Real_GDP','GDP_rank','Percentage_change','Change_rank']
df1=df1.dropna(subset=['County'])
df1.drop(index=df1.index[0], 
        axis=0, 
        inplace=True)
df1 = df1.replace('(NA)',np.nan, regex=True)
df1=df1.dropna(subset=['Percentage_change'])
df1.loc[df1["GDP_rank"]=="--", "State"] = df1["County"]
df1['State']=df1['State'].ffill()
indexGDP = df1[ df1['GDP_rank'] == "--"].index
df1.drop(indexGDP , inplace=True)
df1=df1.fillna(0)
df1=df1.reset_index(drop=True)
df1.to_csv('GDP.csv')

In [375]:
df2=pd.read_excel('income_o.xlsx',skiprows=3,skipfooter=5)
df2.insert(0, "col0",np.nan)
df2=df2[["col0",'Unnamed: 0',2019,'2020.1','2020.2','2020.3']]
df2.columns = ['State','County','Per_capita_personal_income','income_rank','Percentage_change','Change_rank']
df2=df2.dropna(subset=['County'])
df2.drop(index=df2.index[0], 
        axis=0, 
        inplace=True)
df2 = df2.replace('(NA)',np.nan, regex=True)
df2=df2.dropna(subset=['Percentage_change'])
df2.loc[df2["income_rank"]=="--", "State"] = df2["County"]
df2['State']=df2['State'].ffill()

indexGDP = df2[ df2['income_rank'] == "--"].index
df2.drop(indexGDP , inplace=True)
df2=df2.fillna(0)
df2=df2.reset_index(drop=True)
df2.to_csv('income.csv')

In [ ]:
#database website
#https://projec-549db-default-rtdb.firebaseio.com/

In [493]:
requests.delete(url="https://projec-549db-default-rtdb.firebaseio.com/.json")

<Response [200]>

mkdir: create a directory in file system, e.g., mkdir /user/john
ls: listing content of a given directory, e.g., ls /user
cat: display content of a file, e.g., cat /user/john/hello.txt
rm: remove a file from the file system, e.g., rm /user/john/hello.txt
put: uploading a file to file system, e.g., put(
cars.csv, /user/john, k = # partitions) will upload a file cars.csv to the directory /user/john in EDFS. But note that the file should be stored in k partitions, and the file system should remember where the partitions are stored. You should design a method to partition the data. You may also have the user indicate the method, e.g., hashing on certain car attribute, in the put method.
getPartitionLocations(file): this method will return the locations of partitions of the file.
readPartition(file, partition): this method will return the content of partition # of the specified file. The portioned data will be needed in the second task for parallel processing.

In [551]:
def mkdir(directory):
    data="{}"
    jsondata = json.dumps(json.loads(data))
    requests.put(url="https://projec-549db-default-rtdb.firebaseio.com"+directory+".json" , json= jsondata)

def ls(directory):
    list_item=requests.get(url="https://projec-549db-default-rtdb.firebaseio.com"+directory+".json")
    list_item=list(list_item.json().keys())
    for x in list_item:
        print(x)


def put(file,directory,k=1):
    filename=file.split('.')[0]
    for i in range(1,k+1):
        requests.post(url="https://projec-549db-default-rtdb.firebaseio.com"+directory+"/"+filename+".json", json={"p"+str(i):'<https://projec-549db-default-rtdb.firebaseio.com'+'/'+filename+str(i)+".json>"})
## Provide file name with path for example: "C:\Users\xxxxx\flights.csv"
    split_source_file = file

## find number of lines using Pandas
    pd_dataframe = pd.read_csv(split_source_file, header=0)
    number_of_rows = len(pd_dataframe.index) + 1
    headers=list(pd_dataframe.columns)

## find number of lines using traditional python
# fh = open(split_source_file, 'r')
# for count, line in enumerate(fh):
#     pass
# py_number_of_rows = count
#print(f"{number_of_rows}")

## Incase of equal split, provide the same number for min and max
    min_rows = number_of_rows//k+1
    max_rows = number_of_rows//k+3

    file_increment = 1
    skip_rows = 1

## first file random numbers
    number_of_rows_perfile = random.randint(min_rows, max_rows)

    while True:

        if number_of_rows_perfile <= 0:
            break
    ## Read CSV file with number of rows and skip respective number of lines
        df = pd.read_csv(split_source_file, header=None, nrows = number_of_rows_perfile,skiprows = skip_rows)
    ## Target file name
        split_target_file = f"{split_source_file[:-4]}{file_increment}.csv"

    ## write to csv 
        df.to_csv(split_target_file, index=False, header=None, mode='a', chunksize=number_of_rows_perfile)
        
        file_increment += 1

        skip_rows += number_of_rows_perfile

    ## Last file handler
        if skip_rows >= number_of_rows:
            number_of_rows_perfile = number_of_rows - skip_rows
        else:
            number_of_rows_perfile = random.randint(min_rows, max_rows)
    
    for i in range(1,k+1):
        df=pd.read_csv(file.split('.')[0]+str(i)+'.'+file.split('.')[1])
        df.columns=headers
        df=df.to_dict('index')
        rep=requests.put(url="https://projec-549db-default-rtdb.firebaseio.com/"+file.split('.')[0]+str(i)+".json",json= df) 
    

def getPartitionLocations(file):
    list_item=requests.get(url="https://projec-549db-default-rtdb.firebaseio.com"+file[:-4]+".json")
    list_item=list(list_item.json().values())
    ls=[]

    for x in list_item:
        ls.append(list(x.values())[0])
    for x in ls:
        print(x)
    
    
    
def readPartition(file, partition):
    partition_location="https://projec-549db-default-rtdb.firebaseio.com/"+file.split('/')[-1][:-4]+str(partition)+".json"
    partition_content=requests.get(url=partition_location)
    partition_content=partition_content.json()
    jsonData = json.dumps(partition_content, indent=2)
    print(jsonData)
    


    
def cat(file):
    list_item=requests.get(url="https://projec-549db-default-rtdb.firebaseio.com"+file[:-4]+".json")
    list_item=list(list_item.json().values())
    ls=[]
    for x in list_item:
        ls.append(list(x.values())[0][1:-1])
    for x in ls:
        partition_content=requests.get(url=x)
        partition_content=partition_content.json()
        jsonData = json.dumps(partition_content, indent=2)
        print("partition from "+x)
        print(jsonData)

def rm(file):
    list_item=requests.get(url="https://projec-549db-default-rtdb.firebaseio.com"+file[:-4]+".json")
    list_item=list(list_item.json().values())
    ls=[]
    for x in list_item:
        ls.append(list(x.values())[0][1:-1])
    for x in ls:
        requests.delete(url=x)
    requests.delete(url="https://projec-549db-default-rtdb.firebaseio.com"+file[:-4]+".json")




In [496]:
mkdir("/user/john")

In [497]:
ls("/user")

john


In [541]:
put("crime.csv","/user/john",2)

In [499]:
put("income.csv","/user/john",2)

In [500]:
put("GDP.csv","/user/john",2)

In [501]:
getPartitionLocations("/user/john/crime.csv")

<https://projec-549db-default-rtdb.firebaseio.com/crime1.json>
<https://projec-549db-default-rtdb.firebaseio.com/crime2.json>


In [547]:
readPartition("/user/john/crime.csv",1)

[
  {
    "Aggravated_Assault": 103.0,
    "Arson": 6.0,
    "Burglary": 59.0,
    "County": "Coconino",
    "Larceny-theft": 180.0,
    "Motor_vehicle_theft": 25.0,
    "Murder": 6.0,
    "Property_crime": 264.0,
    "Rape": 17.0,
    "Robbery": 1.0,
    "State": "ARIZONA",
    "Unnamed: 0": 1,
    "Violent_Crime": 127.0
  },
  {
    "Aggravated_Assault": 107.0,
    "Arson": 13.0,
    "Burglary": 573.0,
    "County": "Mohave",
    "Larceny-theft": 1197.0,
    "Motor_vehicle_theft": 213.0,
    "Murder": 3.0,
    "Property_crime": 1983.0,
    "Rape": 6.0,
    "Robbery": 19.0,
    "State": "ARIZONA",
    "Unnamed: 0": 2,
    "Violent_Crime": 135.0
  },
  {
    "Aggravated_Assault": 171.0,
    "Arson": 0.0,
    "Burglary": 321.0,
    "County": "Pinal",
    "Larceny-theft": 987.0,
    "Motor_vehicle_theft": 161.0,
    "Murder": 3.0,
    "Property_crime": 1469.0,
    "Rape": 5.0,
    "Robbery": 18.0,
    "State": "ARIZONA",
    "Unnamed: 0": 3,
    "Violent_Crime": 197.0
  },
  {
    "Aggra

In [552]:
cat("/user/john/crime.csv")

partition from https://projec-549db-default-rtdb.firebaseio.com/crime1.json
[
  {
    "Aggravated_Assault": 103.0,
    "Arson": 6.0,
    "Burglary": 59.0,
    "County": "Coconino",
    "Larceny-theft": 180.0,
    "Motor_vehicle_theft": 25.0,
    "Murder": 6.0,
    "Property_crime": 264.0,
    "Rape": 17.0,
    "Robbery": 1.0,
    "State": "ARIZONA",
    "Unnamed: 0": 1,
    "Violent_Crime": 127.0
  },
  {
    "Aggravated_Assault": 107.0,
    "Arson": 13.0,
    "Burglary": 573.0,
    "County": "Mohave",
    "Larceny-theft": 1197.0,
    "Motor_vehicle_theft": 213.0,
    "Murder": 3.0,
    "Property_crime": 1983.0,
    "Rape": 6.0,
    "Robbery": 19.0,
    "State": "ARIZONA",
    "Unnamed: 0": 2,
    "Violent_Crime": 135.0
  },
  {
    "Aggravated_Assault": 171.0,
    "Arson": 0.0,
    "Burglary": 321.0,
    "County": "Pinal",
    "Larceny-theft": 987.0,
    "Motor_vehicle_theft": 161.0,
    "Murder": 3.0,
    "Property_crime": 1469.0,
    "Rape": 5.0,
    "Robbery": 18.0,
    "State": "A

partition from https://projec-549db-default-rtdb.firebaseio.com/crime2.json
[
  {
    "Aggravated_Assault": 0.0,
    "Arson": 0.0,
    "Burglary": 2.0,
    "County": "Franklin",
    "Larceny-theft": 6.0,
    "Motor_vehicle_theft": 2.0,
    "Murder": 0.0,
    "Property_crime": 10.0,
    "Rape": 0.0,
    "Robbery": 0.0,
    "State": "NEBRASKA",
    "Unnamed: 0": 1106,
    "Violent_Crime": 0.0
  },
  {
    "Aggravated_Assault": 2.0,
    "Arson": 0.0,
    "Burglary": 3.0,
    "County": "Frontier",
    "Larceny-theft": 20.0,
    "Motor_vehicle_theft": 1.0,
    "Murder": 0.0,
    "Property_crime": 24.0,
    "Rape": 1.0,
    "Robbery": 0.0,
    "State": "NEBRASKA",
    "Unnamed: 0": 1107,
    "Violent_Crime": 3.0
  },
  {
    "Aggravated_Assault": 5.0,
    "Arson": 0.0,
    "Burglary": 13.0,
    "County": "Furnas",
    "Larceny-theft": 35.0,
    "Motor_vehicle_theft": 9.0,
    "Murder": 0.0,
    "Property_crime": 57.0,
    "Rape": 2.0,
    "Robbery": 0.0,
    "State": "NEBRASKA",
    "Unnamed

In [531]:
rm("/user/john/crime.csv")